### Research Ideas:
- Predict (collector) vinyl price
- https://blog.discogs.com/en/discogs-top-100-most-expensive-records/
- limits: only 100 data points
- can we obtain # copies/presses
- The goal isn't to analyze why recs have gone up in general, but if collector, what are some attributes that may predict the price. OR we can ask what are some attributes that predict the RATINGS of expensive recs

**UPDATED** 
**DISCOGS**
- most expensive lists: https://www.discogs.com/lists?list=expensive+items&page=2
- use this to obtain all years (2010-2019)
- example of month (jan2010): https://www.discogs.com/lists/Most-expensive-items-sold-in-Discogs-Marketplace-for-October-2010/140095
- example of album within month (jan2010): https://www.discogs.com/La-Monte-Young-Drift-Study-43740-50950-PM-5-VIII-68-NYC/release/1512276
- example of 100 expensive from archives: http://web.archive.org/web/20180502225137/https://blog.discogs.com/en/discogs-top-100-most-expensive-records/
- graph of 10 years: https://blog.discogs.com/en/discogs-top-100-most-expensive-records/

**MISC MUSIC**
- vinylfactory: https://thevinylfactory.com/features/online-tools-for-record-collectors/
- links to spotify: http://www.disconest.com/
- discogs misc: https://web.archive.org/web/20210106081812/https://blog.discogs.com/en/
- discogs misc: https://blog.discogs.com/en/vinyl-record-price-guide/
- data: https://www.discogs.com/developers#page:user-collection
- data: https://data.discogs.com/?prefix=data/2020/
- pitchfork: https://pitchfork.com/reviews/best/reissues/?page=1
- spotify github: https://github.com/nsgrantham/pitchfork-reviews
- spotify kaggle: https://www.kaggle.com/yamaerenay/spotify-dataset-19212020-160k-tracks
- spotify medium: https://towardsdatascience.com/step-by-step-to-visualize-music-genres-with-spotify-api-ce6c273fb827
- discogs (full code): http://www.diva-portal.org/smash/get/diva2:1443317/FULLTEXT01.pdf

**NEW LIST - ALL ITEMS. Need to pare down to something specific**
**to consider:**
- vintage vinyl years?
- jazz only?
- certain format?
- create ranking of how many times an arist shows up in list
- differential in haves and wants?
- price history?

- dicogs: lists: https://www.discogs.com/user/discogs/lists?header=1
- https://medium.com/@kdavis7190/vinyl-resale-price-prediction-6cb0adaedcb9
- https://github.com/kdavis01/projects/blob/master/vinyl_resale_regression/Data_Gathering.ipynb


### 1. setup

In [1]:
from bs4 import BeautifulSoup
import requests

## allows us to use reg expressions to search fields
import re
#runtime_regex = re.compile('Run')
#soup.find(text=runtime_regex)

### Function 1 for PRICE only
- this is different because it takes the first instance of the value in the field name
- may need to create a separate function for cleaning this field (no $)

In [354]:
def get_album_price(soup, field_name):
    
    '''
    Grab a value from discogs archive HTML
    Takes a string attribute of an album on the page and returns the string
    We can go directly to the field name using the class element
    
    This will be used for:
        . have, wants, rating, numrating, price
    '''
    obj = soup.find_all(class_=field_name)[0].text
    #print(obj)
    return obj
    if not obj: 
        return None
    
    # this works for most of the values
#     next_element = obj.findNext()
#     print(next_element)
    
#     if next_element:
#         return next_element.text 

#     else:
#         return None

### Function 2 for regular expression items
- the majority of our variables will process through this

In [360]:
def get_album_txt(soup, field_name):
    
    '''Grab a value from discogs archive HTML
    
    Takes a string attribute of an album on the page and returns the string in
    the next sibling object (the value for that attribute) or None if nothing is found.
    '''
    
    obj = soup.find(text=re.compile(field_name))
    
    if not obj: 
        return None
    
    # this works for most of the values
    next_element = obj.findNext()
    
    if next_element:
        return next_element.text 

    else:
        return None

In [510]:
# rated

rating = get_album_txt(soup,'Rated').strip()
#rated = get_album_txt(soup,'Rated').strip()
print(rating)

5.00


In [363]:
# ratings
gen = get_album_txt(soup,'Genre:').strip()
print(gen)

Jazz


### Testing : get votes, haves wants
- this one works but refined futher below

In [586]:
# def get_album_votes(soup, field_name):
    
#     '''Grab a value from discogs archive HTML
#        Takes info in votes containing #votes, haves, wants
#     '''    
#     obj = soup.find(text=re.compile(field_name))
#     return obj
#     if not obj: 
#         return None
    

In [591]:
# string of have/wants, etc. they need to be parsed
votestr = get_album_votes(_soup,'votes')
print(votestr)

 of 33 votes (91 have, 679 want)
                


### Function 3: Grab votes, have, want
- performed parsing of votes field into haves/wants

In [716]:
def get_album_votes(soup, field_name, rtype ):
    
    '''Grab a value from discogs archive HTML
       Takes info in votes containing #votes, haves, wants
    '''    
    obj = soup.find(text=re.compile(field_name))
    #return obj

    if not obj:
        return None
    
    
#     if obj=='No Rating Yet':
#         return None
        
    splitvotes = obj.split('(')[0].strip()
    #print(splitvotes)
    #return splitvotes
    
    # parse votes
    if rtype == 'vote':
        votes = splitvotes.split(' ',1)[1].split(' ',1)[0]
        #print(votes)
        return votes

    # parse haves
    elif rtype=='have':
        splithaves = obj.split('(')[1].strip()
        #print(splithaves)
        #return splithaves
        haves= splithaves.split(',',1)[0].split(' ',1)[0]
        #print(haves)
        return haves
    
    # parse wants
    elif rtype=='want':
        splitwants = obj.split('(')[1].split(',',1)[1].strip()
        #print(splitwants)
        wants = splitwants.split(' ',1)[0]
        #print(wants)
        return wants
        
    else:
        return None
#     # parse wants
#     splitwants = votestr.split('(')[1].split(',',1)[1].strip()
#     wants = splitwants.split(' ',1)[0]
    #print(wants)


In [718]:
# string of have/wants, etc. they need to be parsed
votestr = get_album_votes(_soup,'votes','want')
print(votestr)

43


#### Testing of parsing individually

In [253]:
splitvotes = votestr.split('(')[0].strip()
print(splitvotes)

# parse votes
votes = splitvotes.split(' ',1)[1].split(' ',1)[0]
print(votes)

# parse haves
splithaves = votestr.split('(')[1].strip()
print(splithaves)

haves= splithaves.split(',',1)[0].split(' ',1)[0]
print(haves)

# parse wants
splitwants = votestr.split('(')[1].split(',',1)[1].strip()
wants = splitwants.split(' ',1)[0]
print(wants)

of 30 votes
30
145 have, 559 want)
145
559


#### Testing to get artist, title

In [151]:
#Get title
title_string = soup.find('title').text
artist = title_string.split('-')[0].strip()
title1 = title_string.split('-')[1].strip()
title2 = title1.split(':')[0].strip()
print(artist,title2)

Bill Evans Trio* Waltz For Debby


### II. Testing on one page with list depending on filters

In [719]:
# Jazz bop only
url='https://www.discogs.com/sell/list?sort=price%2Cdesc&limit=250&year1=1900&year2=1970&format=Vinyl&price=over40&genre=Jazz&currency=USD&style=Hard+Bop'
response=requests.get(url)
response.status_code

200

In [720]:
page = response.text

In [721]:
soup = BeautifulSoup(page, "lxml")

In [722]:
print(soup.prettify())

<!DOCTYPE html>
<html class="is_not_mobile needs_reduced_ui" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/">
 <head>
  <meta charset="utf-8"/>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <meta content="en" http-equiv="content-language"/>
  <meta content="no-cache" http-equiv="pragma"/>
  <meta content="-1" http-equiv="expires"/>
  <!-- OneTrust Cookies Consent Notice start -->
  <script charset="UTF-8" data-domain-script="e2e3af03-81d8-4f04-a42d-a3cd6cb9ce35" src="https://cdn.cookielaw.org/scripttemplates/otSDKStub.js" type="text/javascript">
  </script>
  <script ccpa-opt-out-geo="ca" ccpa-opt-out-ids="C0004" ccpa-opt-out-lspa="true" charset="UTF-8" src="https://cdn.cookielaw.org/opt-out/otCCPAiab.js" type="text/javascript">
  </script>
  <meta content="initial-scale=1.0,width=device-width" id="viewport" name="viewport"/>
  <script>
   if (window.innerWidth <= 600) document.getElementById('viewport').setAttribute('

#### Look at rows with 'li' within table block - these are distict per album

In [724]:
# tr tag is for rows
# td is elements within a row (think columns)
#rows = [row for row in soup.find(class_='as_table_block').find_all('a')] 

#rows = [row for row in soup.find(class_='shortcut_navigable').find_all('a')] 
#rows = [row for row in soup.find_all('tr')]  # tr tag is for rows

# works
#rows = [row for row in soup.find(class_='shortcut_navigable')
 #       .find_all('a')[0] #         .text
  #     ]  # tr tag is for rows

rows = [row for row in soup.find(class_='table_block mpitems push_down table_responsive')
        .find_all('tr',class_='shortcut_navigable')]  # tr tag is for rows



#rows = [row for row in soup.find(class_='as_table_block').find_all('h3')[0].find('a')] 
#rows = [row for row in soup.find(class_='listitem_title hide_mobile').find_all('a')]
#rows = [row for row in soup.find(class_='listitem body_row row_with_actions shortcut_navigable').find_all('a')]
#rows[1].find_all('td')[1].find('a')['href']

In [725]:
# We are only looking for the LINK. and inside the link we'll pull data
rows

[<tr class="shortcut_navigable" data-release-id="3384832">
 <td class="item_picture as_float">
 <a class="thumbnail-lazyload" href="/sell/item/1244267034?ev=bp_img"><img alt="Tina Brooks - True Blue for sale" class="marketplace_image" data-src="https://img.discogs.com/RlSw5_2BIL78tsRb5WPd4hsG6G8=/fit-in/300x300/filters:strip_icc():format(jpeg):mode_rgb():quality(40)/discogs-images/R-3384832-1328314224.jpeg.jpg" src="data:image/gif;base64,R0lGODlhAQABAIAAAAAAAP///yH5BAEAAAAALAAAAAABAAEAAAIBRAA7"/></a>
 <div class="hide_mobile community_data_text">
 <div class="community_rating">
             Rated: <strong>4.58</strong>
 </div>
 <div class="community_summary community_fixed_width">
 <div class="community_result">
 <span class="have_indicator" style="width:13.402061855670103%;">
 <span class="community_number">91</span>
 </span>
 <span class="community_label">91 have</span>
 </div>
 <div class="community_result">
 <span class="want_indicator high_want" style="width:100%;">
 <span class="

### Extract list of links for each album/row of data 
- gives specific links to album pages

In [726]:
albumlist = {}

for row in rows[0:10]:
    #print(row)
    items = row.find_all('a')
    #print(items)
    link = row.find('a')['href']
    
    print(link)
    
    title_string = row.find('a',class_='item_description_title').text
    title = title_string.split('-')[0].strip()
    #title = title1.split('/')[0].strip()
    print(title)
    
#     title_string=row.find('').text
#     print(title_string)
#     title=title_string.split('-')[0].strip()        
    #print(title)
    
    #Get title
#     title_string = soup.find('title').text
#     title = title_string.split('-')[0].strip()
    
    
    #print(url)
    
    albumlist[title] = [link] + [title]
#    print(row.find_all('a'))
albumlist

/sell/item/1244267034?ev=bp_img
Tina Brooks
/sell/item/1236925833?ev=bp_img
Cliff Jordan* & John Gilmore
/sell/item/1105531603?ev=bp_img
Freddie Hubbard
/sell/item/1206233138?ev=bp_img
Curtis Fuller
/sell/item/1069322934?ev=bp_img
Lee Morgan
/sell/item/1271008317?ev=bp_img
Cannonball Adderley
/sell/item/786354043?ev=bp_img
Hank Mobley With Donald Byrd And Lee Morgan
/sell/item/1146903229?ev=bp_img
Cliff Jordan* & John Gilmore
/sell/item/1028694831?ev=bp_img
Miles Davis
/sell/item/875179540?ev=bp_img
The Dave Bailey Sextet


{'Tina Brooks': ['/sell/item/1244267034?ev=bp_img', 'Tina Brooks'],
 'Cliff Jordan* & John Gilmore': ['/sell/item/1146903229?ev=bp_img',
  'Cliff Jordan* & John Gilmore'],
 'Freddie Hubbard': ['/sell/item/1105531603?ev=bp_img', 'Freddie Hubbard'],
 'Curtis Fuller': ['/sell/item/1206233138?ev=bp_img', 'Curtis Fuller'],
 'Lee Morgan': ['/sell/item/1069322934?ev=bp_img', 'Lee Morgan'],
 'Cannonball Adderley': ['/sell/item/1271008317?ev=bp_img',
  'Cannonball Adderley'],
 'Hank Mobley With Donald Byrd And Lee Morgan': ['/sell/item/786354043?ev=bp_img',
  'Hank Mobley With Donald Byrd And Lee Morgan'],
 'Miles Davis': ['/sell/item/1028694831?ev=bp_img', 'Miles Davis'],
 'The Dave Bailey Sextet': ['/sell/item/875179540?ev=bp_img',
  'The Dave Bailey Sextet']}

### Scraping Multiple Pages

Now that we have the links for album lists we can visit each link to extract even more information about each record. 

In [343]:
import pandas as pd

In [727]:
albumlist

{'Tina Brooks': ['/sell/item/1244267034?ev=bp_img', 'Tina Brooks'],
 'Cliff Jordan* & John Gilmore': ['/sell/item/1146903229?ev=bp_img',
  'Cliff Jordan* & John Gilmore'],
 'Freddie Hubbard': ['/sell/item/1105531603?ev=bp_img', 'Freddie Hubbard'],
 'Curtis Fuller': ['/sell/item/1206233138?ev=bp_img', 'Curtis Fuller'],
 'Lee Morgan': ['/sell/item/1069322934?ev=bp_img', 'Lee Morgan'],
 'Cannonball Adderley': ['/sell/item/1271008317?ev=bp_img',
  'Cannonball Adderley'],
 'Hank Mobley With Donald Byrd And Lee Morgan': ['/sell/item/786354043?ev=bp_img',
  'Hank Mobley With Donald Byrd And Lee Morgan'],
 'Miles Davis': ['/sell/item/1028694831?ev=bp_img', 'Miles Davis'],
 'The Dave Bailey Sextet': ['/sell/item/875179540?ev=bp_img',
  'The Dave Bailey Sextet']}

### Create DF of dictionary above and Transpose

In [728]:
#alb_102010 = pd.DataFrame(albumlist).T  #transpose
alb = pd.DataFrame(albumlist).T
alb.columns
alb.columns = ['link_stub','artist']
alb

link_stub  \
Tina Brooks                                  /sell/item/1244267034?ev=bp_img   
Cliff Jordan* & John Gilmore                 /sell/item/1146903229?ev=bp_img   
Freddie Hubbard                              /sell/item/1105531603?ev=bp_img   
Curtis Fuller                                /sell/item/1206233138?ev=bp_img   
Lee Morgan                                   /sell/item/1069322934?ev=bp_img   
Cannonball Adderley                          /sell/item/1271008317?ev=bp_img   
Hank Mobley With Donald Byrd And Lee Morgan   /sell/item/786354043?ev=bp_img   
Miles Davis                                  /sell/item/1028694831?ev=bp_img   
The Dave Bailey Sextet                        /sell/item/875179540?ev=bp_img   

                                                                                  artist  
Tina Brooks                                                                  Tina Brooks  
Cliff Jordan* & John Gilmore                                Cliff Jordan* & John Gilmore  
Freddie Hubbard                                                          Freddie Hubbard  
Curtis Fuller                                                              Curtis Fuller  
Lee Morgan                                                                    Lee Morgan  
Cannonball Adderley                                                  Cannonball Adderley  
Hank Mobley With Donald Byrd And Lee Morgan  Hank Mobley With Donald Byrd And Lee Morgan  
Miles Davis                                                                  Miles Davis  
The Dave Bailey Sextet                                            The Dave Bailey Sextet

### Primary function to use the full list of records to scrape individual record info

In [730]:
def get_album_dict(link):
    '''
    From discogs link stub, request html, parse with BeautifulSoup, and
    collect 
        - artist
        - title
        - label
        - format
        - country
        - released
        - genre
        - style
        - haves
        - wants
        - avg rating
        - rates        
        - price
        - media
        - sleeve
        
    Return information as a dictionary.
    '''
    
    base_url = 'https://www.discogs.com'
    
    
    #Create full url to scrape
    url = base_url + link
    #print(url)
    
    #Request HTML and parse
    response = requests.get(url)
    page = response.text
    soup = BeautifulSoup(page,"lxml")

    headers = ['artist',
               'title' ,
               'rlabel',
               'rformat',
               'country',
               'release_dt',
               'genre',
               'style',
               'rating',
               'media',
               'sleeve', 
               'price',
               'votes',
               'haves'# ,
#                'wants'
              ]
    
    #Get title
#     title_string = soup.find('title').text
#     title = title_string.split('-')[0].strip()
    title_string = soup.find('title').text
    
    artist = title_string.split('-')[0].strip()    
    title1 = title_string.split('-')[1].strip()
    title  = title1.split(':')[0].strip()
    #print(artist,title)
    

    #Get label (unicode split - need to figure out how to split)
    rlabel = get_album_txt(soup,'Label:').split(r'-')[0].strip()
    
#     #Get format
    rformat = get_album_txt(soup,'Format:').strip()
    #print(rformat)
    
#     #Get country
    country = get_album_txt(soup,'Country:').strip()
    #print(country)
    
#     #Get release date
    release_dt = get_album_txt(soup,'Released:').strip()
    #print(release_dt)
    
#     #Get genre
    genre = get_album_txt(soup,'Genre:').strip()
    #print(genre)
    
#     #Get style
    style = get_album_txt(soup,'Style:').strip()
    #print(style)
    
#     #Get rating    
    #rating = get_album_txt(soup,'Rated').strip()
    rating = get_album_txt(soup,'Rated')    
    
#     #Media
    media = get_album_txt(soup,'Media:').strip()
    #print(media)
    
#     #Sleeve (issues)
    sleeve = get_album_txt(soup,'Sleeve:').strip()
    #print(sleeve)
    
#     #Price (remove $)
    price = get_album_price(soup,'price')
    #print(price)
    
    
    #votestr = get_album_votes(_soup,'votes')
    votes= get_album_votes(soup,'votes','vote')
    #votestr = get_album_votes(soup,'votes')
    #print(votes)
    
    #splitvotes = votestr.split('(')[0].strip()
#     #print(splitvotes)

#     # parse votes
#     votes = splitvotes.split(' ',1)[1].split(' ',1)[0]
#     #print(votes)

#     # parse haves
#     splithaves = votestr.split('(')[1].strip()
    haves= get_album_votes(soup,'votes','have')

#    haves= splithaves.split(',',1)[0].split(' ',1)[0]
#     #print(haves)

#     # parse wants
#     splitwants = votestr.split('(')[1].split(',',1)[1].strip()
    wants= get_album_votes(soup,'votes','want')
#     wants = splitwants.split(' ',1)[0]
    #print(wants)
    
   #     raw_release_date = get_movie_value(soup,'Release Date').split('\n')[0]
#     release_date = to_date(raw_release_date)
    
    
    #Create album dictionary and return
    album_dict = dict(zip(headers, [artist ,
                                    title ,
                                    rlabel,
                                    rformat,
                                    country,
                                    release_dt,
                                    genre,
                                    style ,
                                    rating, 
                                    media,
                                    sleeve,
                                    price,
                                    votes,
                                    haves#,
#                                     wants
                                   ]))
    return album_dict

#### Call the function to pull data

In [731]:
# LINK_STUB is the added parts to the URL
alb_page_info_list = []

for link in alb.link_stub:
    alb_page_info_list.append(get_album_dict(link))

#### Take a look at data

In [732]:
alb_page_info_list

[{'artist': 'Tina Brooks',
  'title': 'True Blue',
  'rlabel': 'Blue Note \u200e– BLP 4041',
  'rformat': 'Vinyl, LP, Album, Mono',
  'country': 'US',
  'release_dt': '1960',
  'genre': 'Jazz',
  'style': 'Hard Bop',
  'rating': '4.58',
  'media': 'Very Good Plus (VG+)',
  'sleeve': 'What does this condition mean?',
  'price': '$5,000.00',
  'votes': '33',
  'haves': '91'},
 {'artist': 'Cliff Jordan* & John Gilmore',
  'title': 'Blowing In From Chicago',
  'rlabel': 'Blue Note \u200e– BLP 1549',
  'rformat': 'Vinyl, LP, Album, Mono',
  'country': 'US',
  'release_dt': 'May 1957',
  'genre': 'Jazz',
  'style': 'Hard Bop',
  'rating': '4.76',
  'media': 'Very Good Plus (VG+)',
  'sleeve': 'What does this condition mean?',
  'price': '$1,650.00',
  'votes': '17',
  'haves': '83'},
 {'artist': 'Freddie Hubbard',
  'title': 'Hub',
  'rlabel': 'Blue Note \u200e– BST 84115',
  'rformat': 'Vinyl, LP, Album, Stereo',
  'country': 'US',
  'release_dt': '1962',
  'genre': 'Jazz',
  'style': 'Hard

### III. bringing together data

In [733]:
alb_page_info = pd.DataFrame(alb_page_info_list)  #convert list of dict to df
alb_page_info.set_index('artist', inplace=True)

alb_page_info

title  \
artist                                                                                     
Tina Brooks                                                                    True Blue   
Cliff Jordan* & John Gilmore                                     Blowing In From Chicago   
Freddie Hubbard                                                                      Hub   
Curtis Fuller                                                                 The Opener   
Lee Morgan                                                       Search For The New Land   
Cannonball Adderley                                                       Somethin' Else   
Hank Mobley With Donald Byrd And Lee Morgan  Hank Mobley With Donald Byrd And Lee Morgan   
Miles Davis                                       Miles Davis And The Modern Jazz Giants   
The Dave Bailey Sextet                                                             Bash!   

                                                                                        rlabel  \
artist                                                                                           
Tina Brooks                                                              Blue Note ‎– BLP 4041   
Cliff Jordan* & John Gilmore                                             Blue Note ‎– BLP 1549   
Freddie Hubbard                                                         Blue Note ‎– BST 84115   
Curtis Fuller                                                            Blue Note ‎– BLP 1567   
Lee Morgan                                                               Blue Note ‎– BLP 4169   
Cannonball Adderley                          Blue Note ‎– BLP 1595, \n            Blue Note...   
Hank Mobley With Donald Byrd And Lee Morgan                              Blue Note ‎– BLP 1540   
Miles Davis                                                             Prestige ‎– PRESTIGE 3   
The Dave Bailey Sextet                                                    Jazz Line (2) ‎– JAZ   

                                                                      rformat  \
artist                                                                          
Tina Brooks                                            Vinyl, LP, Album, Mono   
Cliff Jordan* & John Gilmore                           Vinyl, LP, Album, Mono   
Freddie Hubbard                                      Vinyl, LP, Album, Stereo   
Curtis Fuller                                          Vinyl, LP, Album, Mono   
Lee Morgan                                             Vinyl, LP, Album, Mono   
Cannonball Adderley                                    Vinyl, LP, Album, Mono   
Hank Mobley With Donald Byrd And Lee Morgan            Vinyl, LP, Album, Mono   
Miles Davis                                  Vinyl, LP, 16 ⅔ RPM, Compilation   
The Dave Bailey Sextet                                       Vinyl, LP, Album   

                                            country release_dt genre  \
artist                                                                 
Tina Brooks                                      US       1960  Jazz   
Cliff Jordan* & John Gilmore                     US   May 1957  Jazz   
Freddie Hubbard                                  US       1962  Jazz   
Curtis Fuller                                    US       1957  Jazz   
Lee Morgan                                       US       1966  Jazz   
Cannonball Adderley                              US   May 1958  Jazz   
Hank Mobley With Donald Byrd And Lee Morgan      US       1957  Jazz   
Miles Davis                                      US       1957  Jazz   
The Dave Bailey Sextet                           US       1961  Jazz   

                                                           style rating  \
artist                                                                    
Tina Brooks                                             Hard Bop   4.58   
Cliff Jordan* & John Gilmore                            Hard Bop   4.76   
Freddi

(Note: the rating is indeed missing from a few of these pages!  How could you fix that?)

We can now match this back up with the movie information collected from the table by merging these dataframes.

### Merge data back with list of artists, titles

In [734]:
alb_mrg = alb.merge(alb_page_info, left_index=True, right_index=True)

alb_mrg

link_stub  \
Tina Brooks                                  /sell/item/1244267034?ev=bp_img   
Cliff Jordan* & John Gilmore                 /sell/item/1146903229?ev=bp_img   
Freddie Hubbard                              /sell/item/1105531603?ev=bp_img   
Curtis Fuller                                /sell/item/1206233138?ev=bp_img   
Lee Morgan                                   /sell/item/1069322934?ev=bp_img   
Cannonball Adderley                          /sell/item/1271008317?ev=bp_img   
Hank Mobley With Donald Byrd And Lee Morgan   /sell/item/786354043?ev=bp_img   
Miles Davis                                  /sell/item/1028694831?ev=bp_img   
The Dave Bailey Sextet                        /sell/item/875179540?ev=bp_img   

                                                                                  artist  \
Tina Brooks                                                                  Tina Brooks   
Cliff Jordan* & John Gilmore                                Cliff Jordan* & John Gilmore   
Freddie Hubbard                                                          Freddie Hubbard   
Curtis Fuller                                                              Curtis Fuller   
Lee Morgan                                                                    Lee Morgan   
Cannonball Adderley                                                  Cannonball Adderley   
Hank Mobley With Donald Byrd And Lee Morgan  Hank Mobley With Donald Byrd And Lee Morgan   
Miles Davis                                                                  Miles Davis   
The Dave Bailey Sextet                                            The Dave Bailey Sextet   

                                                                                   title  \
Tina Brooks                                                                    True Blue   
Cliff Jordan* & John Gilmore                                     Blowing In From Chicago   
Freddie Hubbard                                                                      Hub   
Curtis Fuller                                                                 The Opener   
Lee Morgan                                                       Search For The New Land   
Cannonball Adderley                                                       Somethin' Else   
Hank Mobley With Donald Byrd And Lee Morgan  Hank Mobley With Donald Byrd And Lee Morgan   
Miles Davis                                       Miles Davis And The Modern Jazz Giants   
The Dave Bailey Sextet                                                             Bash!   

                                                                                        rlabel  \
Tina Brooks                                                              Blue Note ‎– BLP 4041   
Cliff Jordan* & John Gilmore                                             Blue Note ‎– BLP 1549   
Freddie Hubbard                                                         Blue Note ‎– BST 84115   
Curtis Fuller                                                            Blue Note ‎– BLP 1567   
Lee Morgan                                                               Blue Note ‎– BLP 4169   
Cannonball Adderley                          Blue Note ‎– BLP 1595, \n            Blue Note...   
Hank Mobley With Donald Byrd And Lee Morgan                              Blue Note ‎– BLP 1540   
Miles Davis                                                             Prestige ‎– PRESTIGE 3   
The Dave Bailey Sextet                                                    Jazz Line (2) ‎– JAZ   

                                                                      rformat  \
Tina Brooks                                            Vinyl, LP, Album, Mono   
Cliff Jordan* & John Gilmore                           Vinyl, LP, Album, Mono   
Freddie Hubbard                                      Vinyl, LP, Album, Stereo   
Curtis Fuller                                          Vinyl, LP, Album, Mono   
Lee Morgan                            

### TESTING

### List page
- this page gives a list of 250 records based on teh filter criteria used
- this is only used for testing on code below

In [6]:
#url='https://www.discogs.com/La-Monte-Young-Drift-Study-43740-50950-PM-5-VIII-68-NYC/release/1512276'
url='https://www.discogs.com/sell/list?sort=price%2Cdesc&limit=250&year1=1900&year2=1970&format=Vinyl&price=over40&genre=Jazz&currency=USD'
response=requests.get(url)
response.status_code

200

In [7]:
page = response.text

In [8]:
soup = BeautifulSoup(page, "lxml")

In [10]:
print(soup.prettify()) ## Makes the code nice

<!DOCTYPE html>
<html class="is_not_mobile needs_reduced_ui" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/">
 <head>
  <meta charset="utf-8"/>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <meta content="en" http-equiv="content-language"/>
  <meta content="no-cache" http-equiv="pragma"/>
  <meta content="-1" http-equiv="expires"/>
  <!-- OneTrust Cookies Consent Notice start -->
  <script charset="UTF-8" data-domain-script="e2e3af03-81d8-4f04-a42d-a3cd6cb9ce35" src="https://cdn.cookielaw.org/scripttemplates/otSDKStub.js" type="text/javascript">
  </script>
  <script ccpa-opt-out-geo="ca" ccpa-opt-out-ids="C0004" ccpa-opt-out-lspa="true" charset="UTF-8" src="https://cdn.cookielaw.org/opt-out/otCCPAiab.js" type="text/javascript">
  </script>
  <meta content="initial-scale=1.0,width=device-width" id="viewport" name="viewport"/>
  <script>
   if (window.innerWidth <= 600) document.getElementById('viewport').setAttribute('

#### .find gives you FIRST instance of tag

In [11]:
soup.find('a')

<a href="/en" id="header_logo" title="Go to Discogs.com homepage">
<img alt="" src="https://a.discogs.com/009ab1c499ab73f8b82cf2e4bf10682b4b668007/images/discogs-white.png?5"/>
</a>

#### .find_all gives ALL instances. you can select instance

In [12]:
soup.find_all('a')[-1]

<a id="footer_menu_link">
<i class="icon icon-chevron-down"></i>
<i class="icon icon-chevron-up"></i>
</a>

#### Extracting things like HREF from an element in HTML

In [13]:
testing = soup.find_all('a')[-1]

In [14]:
testing.get("href")

### Test on individual record
- this gives an idea of each record that is clicked and the info in it

In [713]:
url='https://www.discogs.com/sell/item/1236925833'
response=requests.get(url)
response.status_code

200

In [714]:
_page = response.text

In [715]:
_soup = BeautifulSoup(_page, "lxml")

#### Based on function for album price

In [355]:
# string of have/wants, etc. they need to be parsed
price = get_album_price(soup,'price')
print(price)

$749.99


In [356]:
#Get domestic gross
def get_album_txt2(soup, field_name):
    r = (soup.find_all(class_=field_name)[0]).text
    return r
get_album_txt2(soup,'price')   

'$749.99'

In [357]:
# string of have/wants, etc. they need to be parsed
# potentially separate way to get ratings 
rateetc = get_album_price(soup,'rating_value_sm')
print(rateetc)

4.90


In [358]:
rs = soup.find(text=re.compile('Rated'))
next_element = rs
next_element2 = next_element.findNext()    
print(next_element2)

<span class="rating_value_sm">4.90</span>


#### Votes gives us the info we need for votes and haves/wants

In [359]:
print(soup.find(text=re.compile('votes')))

 of 30 votes (145 have, 559 want)
                


In [365]:
# country
country = get_album_txt(soup,'Country:').strip()
print(country)

US


In [527]:
# media condition
media = get_album_txt(soup,'Media:').strip()
print(media)

Very Good Plus (VG+)


In [526]:
sleeve = get_album_txt(soup,'Sleeve:').strip()
print(sleeve)

Poor (P)


In [459]:
# media condition
rlabel = get_album_txt(soup,'Label:').strip()
print(rlabel)

Apollo Records (2)


In [368]:
# votes, haves, wants
votes = get_album_txt(soup,'votes').strip()
print(votes)

Sales History


### Testing : get votes, haves wants
- this one works but refined futher below

In [586]:
# def get_album_votes(soup, field_name):
    
#     '''Grab a value from discogs archive HTML
#        Takes info in votes containing #votes, haves, wants
#     '''    
#     obj = soup.find(text=re.compile(field_name))
#     return obj
#     if not obj: 
#         return None
    

In [591]:
# string of have/wants, etc. they need to be parsed
votestr = get_album_votes(_soup,'votes')
print(votestr)

 of 33 votes (91 have, 679 want)
                


### LECTURES:
- linear regression
- cross validation<br>
    . 80% training<br>
    . 20% testing<br>
- categorical (one hot encoding)
- continuous - standardize (z scores?)


#### testing how this function works

looping through append put replace 
tutorilal - section 
webmojo - base url - indiv 
made list of extra part of link appended

tutorial scrape
. 

for loop for indiidual pages
list of ind link stub
. for loop -f


